# Giriş

13/02/2021 - [@mebaysan](https://github.com/mebaysan)

Bu notebook'da [Plotly](https://plotly.com/python/) kullanarak [choropleth](https://plotly.com/python/choropleth-maps/) harita yapımını öğrenmeye çalışacağız.

- [GitHub gist'lerim](https://gist.github.com/mebaysan/f296ff7d603f973f7a6b1dff39c69596) üzerinden harita oluşturmak için kullanabileceğiniz hazır scriptlere ulaşabilirsiniz.
- Türkiye illeri için **GeoJSON** dosyasına erişmek için [burayı](https://gist.github.com/mebaysan/9be56dd1ca5659c0ff7ea5e2b5cf6479) kullanabilirsiniz.
- Türkiye'ye ait **tüm ilçelere** ve coğrafi bilgilerine CSV olarak erişmek için [burayı](https://gist.github.com/mebaysan/3246378ebce34a67106dcf5271771f4a), JSON olarak erişmek için [burayı](https://gist.github.com/mebaysan/b9f3cc1ad9c1f4294a0a7c7a7be9ec62) kullanabilirsiniz.
- Türkiye **tüm illere** ve coğrafi bilgilerine CSV olarak erişmek için [burayı](https://gist.github.com/mebaysan/7a4ba8531187fa8703ff1f22692d5fa6), JSON olarak erişmek için [burayı](https://gist.github.com/mebaysan/4153d60270167f5245f89c9b8efaec9d) kullanabilirsiniz.

## Plotly Choropleth Hk.

Plotly Choropleth harita oluşturmak istiyorsak çalışacağımız bölge ile ilgili **GeoJSON** dosyasına sahip olmamız gerekmektedir.

Choropleth haritalar hakkında daha detaylı bilgiyi almak için [buraya](https://datavizcatalogue.com/TR/yontemleri/koroplet_harita.html) bakabilirsiniz.

## Notebook Hk.

Haritamızı oluştururken [veri setini kullanacağız](https://www.citypopulation.de/en/turkey/admin/).

Bu veri seti belirli yıl aralıklarında Türkiye'deki toplam nüfusun tahminini içermektedir.

Veri setine [buradan](https://docs.google.com/spreadsheets/d/1iwe7WoUGxl9EkzJwvpw4Fzo_AUh8jjPuHCtJLkZgcLE/edit?usp=sharing) erişebilirsiniz.

GeoJSON için giriş bölümünde bahsettiğimiz GeoJSON dosyasını kullanacağız.

Oluşturduğumuz harita illerdeki tahmini nüfusları gösterecek.

# Ön Hazırlıklar

## Kullanacağımız Paketleri Import Ediyoruz

In [31]:
import pandas as pd  # pip install pandas
import numpy as np  # pip install numpy
import plotly.express as px  # pip install plotly
import plotly.graph_objects as go  # pip install plotly
# pip install plotly | subplot'lar yapmak için kullanacağız
from plotly.subplots import make_subplots
import requests  # pip install requests
import json

## Veri Setlerimizi Yüklüyoruz

### Nüfus Tahminlerine Ait Olan Veri Seti

- Bu notebook'un dizininde bulunan **'Turkey Districts - Population Estimate - Sayfa1.csv'** dosyası

In [32]:
df = pd.read_csv('Turkey Districts - Population Estimate - Sayfa1.csv')

### İllere ait GeoJSON'u Gist Üzerinden Çekeceğiz

In [33]:
response = requests.get(
    'https://gist.githubusercontent.com/mebaysan/9be56dd1ca5659c0ff7ea5e2b5cf6479/raw/6d7a77d8a2892bd59f401eb87bd82d7f48642a58/turkey-geojson.json')
# Gist üzerindeki raw dataya erişmek için adrese istek (get) atıyoruz

In [34]:
# dönen response içerisindeki json'u değişkene atıyoruz ki bu json bizim istediğimiz GeoJSON
geojson = response.json()

# Veri Setlerini İnceleyelim - Düzenleyelim

## Nüfus Tahminleri

In [36]:
df.describe().T  # veri seti hakkında betimsel istatistikler

count unique       top freq
Name                        1055    982    Merkez   51
Status                      1055      4  District  973
Population\nEstimate\n2009  1055   1019       ...   32
Population\nEstimate\n2013  1055   1046    23,066    2
Population\nEstimate\n2019  1055   1052    34,343    2

In [37]:
df.info()  # değişkenler hakkında bilgiler

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1055 entries, 0 to 1054
Data columns (total 5 columns):
 #   Column                    Non-Null Count  Dtype 
---  ------                    --------------  ----- 
 0   Name                      1055 non-null   object
 1   Status                    1055 non-null   object
 2   Population
Estimate
2009  1055 non-null   object
 3   Population
Estimate
2013  1055 non-null   object
 4   Population
Estimate
2019  1055 non-null   object
dtypes: object(5)
memory usage: 41.3+ KB


In [38]:
df.dtypes  # değişkenlere ait veri tipleri
# Burada görüyoruz ki Nüfus tahminleri object olarak gözükmekte. Bunları integer olarak güncellemeliyiz

Name                          object
Status                        object
Population\nEstimate\n2009    object
Population\nEstimate\n2013    object
Population\nEstimate\n2019    object
dtype: object

In [39]:
df.rename(columns={'Population\nEstimate\n2009': 'Tahmin-2009',
                   'Population\nEstimate\n2013': 'Tahmin-2013',
                   'Population\nEstimate\n2019': 'Tahmin-2019'
                   }, inplace=True)
# Değişkenlere daha rahat erişebilmek için isimlerini değiştiriyoruz

In [9]:
df.head(2)

Name                 Status Tahmin-2009 Tahmin-2013 Tahmin-2019
0   Adana  Metropolitan Province   2,062,226   2,149,260   2,237,940
1  Aladağ               District      17,494      17,221      16,121

In [40]:
# excelden aldığımız veri setinde ondalıkları ',' ile ayırmışlar fakat biz bunları python'da '.' ile yapıyoruz
# ilgili değişkeni ',' ile ayırıp bir listeye atıyoruz, sonra ayırdığımız elemanları yanyana dizerek bir **string** oluşturuyoruz
df['Tahmin-2009'] = df['Tahmin-2009'].apply(lambda x: ''.join(x.split(',')))
df['Tahmin-2013'] = df['Tahmin-2013'].apply(lambda x: ''.join(x.split(',')))
df['Tahmin-2019'] = df['Tahmin-2019'].apply(lambda x: ''.join(x.split(',')))

In [41]:
# Veri setimizde bazı satırlarda null olan değerleri '...' girmişler. Bunları np.nan ile değiştiriyoruz, bu sayede string değerleri numeric yaparken zorlanmayacağız
df.replace('...', np.nan, inplace=True)

In [42]:
# string olan değişkenleri numeric olarak düzenliyoruz
df['Tahmin-2009'] = pd.to_numeric(df['Tahmin-2009'])
df['Tahmin-2013'] = pd.to_numeric(df['Tahmin-2013'])
df['Tahmin-2019'] = pd.to_numeric(df['Tahmin-2019'])

In [43]:
df.dtypes  #  gördüğümüz gibi numeric olarak gelmekteler

Name            object
Status          object
Tahmin-2009    float64
Tahmin-2013      int64
Tahmin-2019      int64
dtype: object

Şimdi ise veri setinde **Status** değişkeni `Metropolitan Province` veya `Province` olanları filtereleyeceğiz.

Bu sayede veri setimizdeki şehirleri ayırabileceğiz.

In [44]:
df = df[(df['Status'] == 'Metropolitan Province')
        | (df['Status'] == 'Province')]

In [45]:
df

Name                 Status  Tahmin-2009  Tahmin-2013  \
0              Adana  Metropolitan Province    2062226.0      2149260   
16          Adıyaman               Province     588475.0       597184   
26    Afyonkarahisar               Province     701326.0       707123   
45              Ağrı               Province     537665.0       551177   
54           Aksaray               Province     376907.0       382806   
...              ...                    ...          ...          ...   
1002            Uşak               Province      33586.0       346508   
1009             Van  Metropolitan Province    1022310.0      1070113   
1023          Yalova               Province     202531.0       220122   
1030          Yozgat               Province     487365.0       444211   
1045       Zonguldak               Province     619812.0       601567   

      Tahmin-2019  
0         2237940  
16         626465  
26         729483  
45         536199  
54         416367  
...           ...  
1002       370509  
1009      1136757  
1023       270976  
1030         4212  
1045       596053  

[81 rows x 5 columns]

## GeoJSON

In [46]:
# ile koordinatların tutulduğu array'e ulaşırız. Plotly Choropleth ile oluştururken otomatik olarak bu array'e bakıyor.
geojson['features']

[{'geometry': {'type': 'MultiPolygon',
   'coordinates': [[[[35.279026031494084, 36.64069366455101],
      [35.28180694580078, 36.6390266418457],
      [35.282917022705135, 36.636806488037166],
      [35.27819442749029, 36.640140533447266],
      [35.279026031494084, 36.64069366455101]]],
    [[[35.27152633666998, 36.64485931396507],
      [35.274028778076456, 36.64319610595709],
      [35.274028778076456, 36.64208221435558],
      [35.27125167846697, 36.64319610595709],
      [35.27152633666998, 36.64485931396507]]],
    [[[35.20735931396513, 36.65069580078119],
      [35.2093048095706, 36.64986038208025],
      [35.20958328247099, 36.64930725097685],
      [35.206249237060604, 36.649028778076456],
      [35.20735931396513, 36.65069580078119]]],
    [[[35.21180725097656, 36.65541839599638],
      [35.212081909179744, 36.65319442749046],
      [35.21152877807634, 36.6529159545899],
      [35.20958328247099, 36.65513992309582],
      [35.21180725097656, 36.65541839599638]]],
    [[[35.2

In [47]:
geojson['features'][0]  # İlk şehre ait geojson özellikleri

{'geometry': {'type': 'MultiPolygon',
  'coordinates': [[[[35.279026031494084, 36.64069366455101],
     [35.28180694580078, 36.6390266418457],
     [35.282917022705135, 36.636806488037166],
     [35.27819442749029, 36.640140533447266],
     [35.279026031494084, 36.64069366455101]]],
   [[[35.27152633666998, 36.64485931396507],
     [35.274028778076456, 36.64319610595709],
     [35.274028778076456, 36.64208221435558],
     [35.27125167846697, 36.64319610595709],
     [35.27152633666998, 36.64485931396507]]],
   [[[35.20735931396513, 36.65069580078119],
     [35.2093048095706, 36.64986038208025],
     [35.20958328247099, 36.64930725097685],
     [35.206249237060604, 36.649028778076456],
     [35.20735931396513, 36.65069580078119]]],
   [[[35.21180725097656, 36.65541839599638],
     [35.212081909179744, 36.65319442749046],
     [35.21152877807634, 36.6529159545899],
     [35.20958328247099, 36.65513992309582],
     [35.21180725097656, 36.65541839599638]]],
   [[[35.21347045898466, 36.6598

In [48]:
geojson['features'][0]['id']  # ilk şehre ait geojson id'si

1

In [49]:
geojson['features'][0]['properties']  # ilk şehre ait geojson properties'i

{'name': 'Adana'}

In [50]:
# ilk şehre ait geojson properties name'i
geojson['features'][0]['properties']['name']
# bu properties altındaki özellikleri choropleth ile bind ederek istediğimiz properties'e göre harita oluşturabiliriz

'Adana'

<p style='color:red;'>Plotly Choropleth default olarak feautures altındaki objenin id'sine bakar.</p>

<p style='color:red;'>Biz istersek bunu properties altındaki özellikler ile yapmasını söyleyebiliriz.</p>

<p style='color:red;'>Fakat bunu bilmediğimizi varsayalım, id ile elimizdeki veri setindeki şehir adlarını bağlamak için geoDict adında bir değişken oluşturalım ve bu dict içerisinde şehir adı karşısında ilgili olduğu geojson objesinin id'si bulunsun.</p>

In [51]:
geoDict = {}

In [52]:
for i in geojson['features']:
    geoDict[i['properties']['name']] = i['id']

In [53]:
geoDict  # Artık her şehrin ait olduğu GeoJSON objesine karşılık gelen id'e sahibiz. Dilersek bunları df veri setimiz ile bağlayabiliriz

{'Adana': 1,
 'Adıyaman': 2,
 'Afyon': 3,
 'Ağrı': 4,
 'Aksaray': 5,
 'Amasya': 6,
 'Ankara': 7,
 'Antalya': 8,
 'Ardahan': 9,
 'Artvin': 10,
 'Aydın': 11,
 'Balıkesir': 12,
 'Bartın': 13,
 'Batman': 14,
 'Bayburt': 15,
 'Bilecik': 16,
 'Bingöl': 17,
 'Bitlis': 18,
 'Bolu': 19,
 'Burdur': 20,
 'Bursa': 21,
 'Çanakkale': 22,
 'Çankırı': 23,
 'Çorum': 24,
 'Denizli': 25,
 'Diyarbakır': 26,
 'Düzce': 27,
 'Edirne': 28,
 'Elazığ': 29,
 'Erzincan': 30,
 'Erzurum': 31,
 'Eskişehir': 32,
 'Gaziantep': 33,
 'Giresun': 34,
 'Gümüşhane': 35,
 'Hakkari': 36,
 'Hatay': 37,
 'Iğdır': 38,
 'Isparta': 39,
 'İstanbul': 40,
 'İzmir': 41,
 'Kahramanmaraş': 42,
 'Karabük': 43,
 'Karaman': 44,
 'Kars': 45,
 'Kastamonu': 46,
 'Kayseri': 47,
 'Kilis': 48,
 'Kırıkkale': 49,
 'Kırklareli': 50,
 'Kırşehir': 51,
 'Kocaeli': 52,
 'Konya': 53,
 'Kütahya': 54,
 'Malatya': 55,
 'Manisa': 56,
 'Mardin': 57,
 'Mersin': 58,
 'Muğla': 59,
 'Muş': 60,
 'Nevşehir': 61,
 'Niğde': 62,
 'Ordu': 63,
 'Osmaniye': 64,
 'Rize':

## Veri Seti ile GeoJSON id'leri Eşleştirelim

In [54]:
# başlangıç için basit bir değişken ekledik ve tüm satırlar için değerini Yok olarak belirledik
df.loc[:, 'GeoID'] = 'Yok'

In [55]:
# df içerisindeki bu 3 ilimizi geoDict içerisindeki isimleri ile değiştiriyoruz
df.loc[df['Name'] == 'Afyonkarahisar'] = df.loc[df['Name']
                                                == 'Afyonkarahisar'].replace('Afyonkarahisar', 'Afyon')
df.loc[df['Name'] == 'Elâzığ'] = df.loc[df['Name']
                                        == 'Elâzığ'].replace('Elâzığ', 'Elazığ')
df.loc[df['Name'] == 'Hakkâri'] = df.loc[df['Name']
                                         == 'Hakkâri'].replace('Hakkâri', 'Hakkari')

In [56]:
# geoDict içerisindeki ID'lerini veri setimizde ilgili il için bir değişken olarak ekliyoruz
df['GeoID'] = df['Name'].apply(lambda x: geoDict[x])

In [57]:
df.head(1)

Name                 Status  Tahmin-2009  Tahmin-2013  Tahmin-2019  GeoID
0  Adana  Metropolitan Province    2062226.0      2149260      2237940      1

# Choropleth Harita Yapımı

## Plotly Express ile Choropleth Haritalar

### Choropleth MapBox

- Choropleth MapBox; Plotly'nin [MapBox](https://www.mapbox.com/) haritaları ile kullanmak için oluşturduğu objelerdir. Platform üzerinden oluşturduğunuz token'lar ile kendi özel haritalarınızı kullanabilirsiniz.

In [63]:
fig = px.choropleth_mapbox(df,  # hangi veri seti
                           geojson=geojson,  # hangi geojson dosyası
                           locations='GeoID',  # geojson dosyasında id'e denk gelen, veri setindeki hangi değişken
                           color='Tahmin-2019',  # hangi Değişkene göre renk paleti
                           color_continuous_scale="dense",  # hangi renk paleti
                           # renklendirme için min ve max değerler aralığı
                           range_color=(df['Tahmin-2019'].min(),
                                        df['Tahmin-2019'].max()),
                           # map başlangıç lat & lon
                           center={'lat': 38.7200, 'lon': 34.0000},
                           # labellar değişecek mi
                           labels={'Tahmin-2019': '2019 Nüfus Tahmini'},
                           mapbox_style="carto-positron",  # mapbox stil
                           zoom=4.8,  # yakınlık
                           opacity=0.5,  # opacity
                           custom_data=[df['Name'],
                                        df['Tahmin-2019'], df['Status']]  # figure'e göndereceğimiz ekstra veriler
                           )
fig.update_layout(title='Türkiye Nüfus Tahminleri 2019',  # figure başlığı
                  title_x=0.5  # Title'ın x eksenindeki pozisyonu
                  )
#  gönderdiğimiz customdata'nın ilk elemanı
hovertemp = '<i style="color:red;">Şehir Adı:</i> %{customdata[0]}<br>'
hovertemp += '<i>Şehir Statüsü:</i> %{customdata[2]}<br>'
hovertemp += '<i>Tahmini Nüfus:</i> %{customdata[1]:,f}<br>'
# figure üzerine gelince oluşturduğum stringi göster
fig.update_traces(hovertemplate=hovertemp)
fig.show()

### Choropleth

In [69]:
fig = px.choropleth(df,  # hangi veri seti
                    geojson=geojson,  # hangi geojson dosyası
                    locations='Name',  # featureidkey ile belirtilen özelliğe denk gelen değişken
                    # locations değişkeni ile geojson'daki hangi özelliği bağlayacağız
                    featureidkey='properties.name',
                    color='Tahmin-2019',  # hangi Değişkene göre renk paleti
                    color_continuous_scale="Viridis",  # hangi renk paleti
                    # renklendirme için min ve max değerler aralığı
                    range_color=(df['Tahmin-2019'].min(),
                                 df['Tahmin-2019'].max()),
                    # map başlangıç lat & lon
                    center={'lat': 38.7200, 'lon': 34.0000},
                    # labellar değişecek mi
                    labels={'Tahmin-2019': '2019 Nüfus Tahmini'},
                    custom_data=[df['Name'],
                                 df['Tahmin-2019'], df['Status']]  # figure'e göndereceğimiz ekstra veriler
                    )
fig.update_geos(fitbounds="locations",  # harita sınırları
                visible=False  # sınırların gözüküp gözükmemesi
                )

#  gönderdiğimiz customdata'nın ilk elemanı
hovertemp = '<i>Şehir Adı:</i> %{customdata[0]}<br>'
hovertemp += '<i>Şehir Statüsü:</i> %{customdata[2]}<br>'
hovertemp += '<i>Tahmini Nüfus:</i> %{customdata[1]:,f}<br>'
# figure üzerine gelince oluşturduğum stringi göster
fig.update_traces(hovertemplate=hovertemp)
fig.show()

## Plotly Graph Objects ile Choropleth Haritalar

## Subplot'lar ile Choropleth Haritalar Yapalım

- <p style='color:red;'>Unutmayalım ki subplot'lar ile çalışırken bu dökümanı hazırladığımız zamanlarda <b>make_subplot</b> fonksiyonu plotly express altındaki figürleri desteklememektedir.</p>
- Subplotları oluşturmak için **Plotly Graph Objects**'i kullanmamız gerekmektedir.

In [72]:
fig = make_subplots(  # subplot oluşturmamızı sağlayan fonksiyon
    rows=1, cols=2,  # 1 satır 2 kolonluk bir zemin (figür) hazırlıyoruz
    specs=[
        [
            # satırlar içerisindeki sütunları dict olarak vermeliyiz, 1. satır 1. sütun
            {"type": "choropleth"},
            {"type": "choropleth"}  # 1. satır 1. sütun
        ],  # satırları listeler (vektör) olarak vermemiz gerekmekte, 1. satır
    ]
)

fig.add_trace(trace=go.Choropleth(
    featureidkey='properties.name',
    geojson=geojson,
    locations=df['Name'],
    z=df['Tahmin-2009'],
    colorscale='YlGn',
    colorbar_title="Tahmin",
    zmin=df['Tahmin-2009'].min(),
    zmax=df['Tahmin-2009'].max(),
    name='2009 Nüfus Tahmini',
    hoverinfo='location+z',
    showlegend=False,  # bu choropleth'e ait renk bar'ı saklıyoruz
    # bu choropleth'e ait sayısal renk değerlerini (aralıklar) saklıyoruz
    showscale=False,
), row=1, col=1)  # oluşturduğumuz zeminin (figür) 1. satır 1. sütununa Choropleth ekliyoruz


fig.add_trace(trace=go.Choropleth(
    featureidkey='properties.name',
    geojson=geojson,
    locations=df['Name'],
    z=df['Tahmin-2019'],
    colorscale='YlGn',
    colorbar_title="Tahmin",
    zmin=df['Tahmin-2019'].min(),
    zmax=df['Tahmin-2019'].max(),
    name='2019 Nüfus Tahmini',
    hoverinfo='location+z',
), row=1, col=2)  # oluşturduğumuz zeminin (figür) 1. satır 2. sütununa Choropleth ekliyoruz

fig.update_geos(fitbounds="locations",
                visible=False,
                )
hovertemp = '<i>Şehir Adı:</i> %{location} <br>'
hovertemp += '<i>Nüfus Tahmini:</i> %{z:,}'
fig.update_traces(hovertemplate=hovertemp)
fig.update_layout(
    title='2009 ve 2019 Arasında Karşılaştırmalı Nüfus Tahminleri', title_x=0.5)
fig.show()